### Notebook for lieselhughes.com/posts/stuff/deneb-made-easy-with-altair/

Install these deps:
```
%pip install pythonnet 
%pip install altair 
%pip install dpath
```

In [ ]:
import sys
sys.path.append(os.path.abspath("python-ssas"))

import pandas as pd
import altair as alt

import ssas_api as ssas

ssas._load_assemblies()


Find the port below with this Powershell:
```Get-NetTcpConnection -OwningProcess $(Get-Process msmdsrv).Id -State Listen```


In [ ]:
global System, DataTable, AMO, ADOMD

import System
from   System.Data import DataTable
import Microsoft.AnalysisServices.Tabular as TOM
import Microsoft.AnalysisServices.AdomdClient as ADOMD


conn = ssas.set_conn_string(
    server="localhost:63045",
    db_name="",
    username="",
    password=""
    )

TOMServer = TOM.Server()
TOMServer.Connect(conn)
print("Connection Successful.")
    


In [ ]:
qry = """
EVALUATE
    SUMMARIZECOLUMNS(
      'Date'[Month],
      TREATAS({"FY2019"}, 'Date'[Fiscal Year]),
      "Sales Amount", CALCULATE(SUM('Sales'[Sales Amount])),
      "Sales Amount by Due Date", 'Sales'[Sales Amount by Due Date]
    )

ORDER BY
  'Date'[Month]
""" 


df = (ssas.get_DAX(
         connection_string=conn, 
         dax_string=qry)
    )

df.head()




In [ ]:

df.columns = [ 'Month' , 'Sales Amount', 'Sales Amount by Due Date' ]
df['Month'] = pd.to_datetime(df['Month'])

df.head()

In [ ]:

df2 = df.melt(id_vars='Month', var_name='Measure', value_name='Value')

df2

In [ ]:
df_long = df.melt(id_vars='Month', var_name='Measure', value_name='Value')

chart = alt.Chart(df_long
    ).mark_area(
        opacity=0.3, 
        line = alt.LineConfig(opacity=1)
    ).encode(
        x='Month:T',
        y=alt.Y('Value:Q',stack=None),
        color='Measure:N'
    )

chart

In [ ]:
chart = alt.Chart(df
    ).transform_fold (
        list(df.columns[1:]),
        as_=['Measure', 'Value']
    ).mark_area(
        opacity=0.3, 
        line = alt.LineConfig(opacity=1)
    ).encode(
        x='Month',
        y=alt.Y('Value:Q',stack=None),
        color='Measure:N'
    )

chart

In [ ]:
colours = [ '#7fc97f', '#beaed4'] 

chart = alt.Chart(df
    ).mark_area(
        opacity=0.5,
        line = alt.LineConfig(opacity=1)
    ).encode(
        x=alt.X('Month', type='temporal', title='Month'),
        y=alt.Y(alt.repeat("layer"),type='quantitative', stack=None),
        color=alt.ColorDatum(alt.repeat("layer"))
    ).repeat(
        layer=list(df.columns[1:])
    ).configure_range(
        category=alt.RangeScheme(colours)
    )

chart



In [ ]:
chart = alt.Chart(df
    ).transform_fold(
        list(df.columns[1:]),
        as_=['Measure', 'Value']
    ).transform_filter(
            f'datum.Measure==="Sales Amount"'
    ).mark_area(
            line = alt.LineConfig(opacity=1, color="red"),
            color=alt.Gradient(
            gradient='linear',
            stops=[
                alt.GradientStop(color='white', offset=0),
                alt.GradientStop(color='red', offset=1)
            ],
            x1=1,
            x2=1,
            y1=1,
            y2=0
        )
    ).encode(
        x=alt.X('Month', type='temporal', title='Month'),
        y=alt.Y('Value',type='quantitative', title='Amount'),
    )
        


chart

In [ ]:
def make_gradient_chart(chart, col, colour):
    return  base.transform_filter(
             f'datum.Measure==="{col}"'
        ).mark_area(
              line = alt.LineConfig(opacity=1, color=colour),
              color=alt.Gradient(
                gradient='linear',
                stops=[
                    alt.GradientStop(color='white', offset=0),
                    alt.GradientStop(color=colour, offset=1)
                ],
                x1=1,
                x2=1,
                y1=1,
                y2=0
            )
        ).encode(
            alt.Stroke(
                'Measure:O', 
            scale=alt.Scale(
                domain=measureCols, 
                range=colours
                )
            )
        )



colours = [ '#7fc97f', '#beaed4']  
measureCols = list(df.columns[1:])  

   
base = alt.Chart(df
    ).transform_fold(
        measureCols,
        as_=['Measure', 'Value']
    ).encode(
        x=alt.X('Month', type='temporal', title='Month'),
        y=alt.Y('Value',type='quantitative', title='Amount')
    )       

chart = alt.layer(
    *[make_gradient_chart(
        base, 
        df.columns[n], 
        colours[n-1]) 
      for n in range(1, df.shape[1])
      ]
)


chart


In [ ]:
import json
#https://github.com/dpath-maintainers/dpath-python
import dpath.util as dpath

dict = chart.to_dict()

dpath.set(dict, '**/data/name', 'dataset')
dpath.delete(dict, 'datasets')
dpath.delete(dict, '$schema')

with open("chart.json", "w") as fp:
    json.dump(dict , fp, indent = 4) 

